### Trying on 2 audio files only

In [5]:
import pandas as pd

In [5]:
d1 = pd.read_csv(r"D:\GP1\.venv\ipynb_Files\Code\training-4whisper.csv")
th = d1[:2]
type(th)

pandas.core.frame.DataFrame

In [6]:
d2 = pd.read_csv(r"D:\GP1\.venv\ipynb_Files\Code\testing-4whisper.csv")
th2 = d2[:2]
type(th2)

pandas.core.frame.DataFrame

In [7]:
th.to_csv('just-train.csv', index=False)
th2.to_csv('just-test.csv', index=False)

In [8]:
from datasets import Features, Value, Audio, load_dataset

sample_data = load_dataset(
    'csv', data_files={
        'train': 'just-train.csv', 
        'test': 'just-test.csv',
    }
)


Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [9]:

features = Features(
    {
        "Transcripts": Value("string"), 
        "Audio_File": Value('string'),
        "TA_ID": Value("int32"),
        "audio": Audio(sampling_rate=16000),
        "audio_wav": Audio(sampling_rate=16000)
    }
)


In [10]:
sample_data = sample_data.cast(features)
sample_data

Casting the dataset:   0%|          | 0/2 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/2 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 2
    })
    test: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 2
    })
})

In [11]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")
feature_extractor

WhisperFeatureExtractor {
  "chunk_length": 30,
  "feature_extractor_type": "WhisperFeatureExtractor",
  "feature_size": 80,
  "hop_length": 160,
  "n_fft": 400,
  "n_samples": 480000,
  "nb_max_frames": 3000,
  "padding_side": "right",
  "padding_value": 0.0,
  "processor_class": "WhisperProcessor",
  "return_attention_mask": false,
  "sampling_rate": 16000
}

In [12]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Arabic", task="transcribe", )

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [13]:
input_str = sample_data["train"][0]["Transcripts"]
labels = tokenizer(input_str).input_ids
decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")



Input:                  قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
Decoded w/ special:    <|startoftranscript|><|ar|><|transcribe|><|notimestamps|> قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم

In [14]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Arabic", task="transcribe")

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [15]:
sample_data = sample_data.remove_columns("audio")
sample_data

DatasetDict({
    train: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio_wav'],
        num_rows: 2
    })
    test: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio_wav'],
        num_rows: 2
    })
})

In [16]:
from datasets import Audio

sample_data = sample_data.cast_column("audio_wav", Audio(sampling_rate=16000))
sample_data['train'][0]

{'Transcripts': ' قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            ',
 'Audio_File': ' https://www.ireadarabic.com/uploads/slides/528/8449895552ae0361f230c080dc19096f.mp3',
 'TA_ID': 81615,
 'audio_wav': {'path': 'D:\\GP1\\.venv\\ipynb_Files\\Code\\tr

In [17]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio_wav"]


    # print(audio['array'])
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    # encode target text to label ids 
    
    batch["labels"] = tokenizer(batch["Transcripts"]).input_ids
    # check.append(batch["labels"])
    
    return batch


In [23]:
sample_data['train']['input_features']

[[[-0.6699848175048828,
   -0.6699848175048828,
   -0.6699848175048828,
   -0.19645404815673828,
   -0.6075112819671631,
   -0.37027502059936523,
   -0.6699848175048828,
   0.14419478178024292,
   0.38477665185928345,
   0.346186101436615,
   -0.03988373279571533,
   0.027289509773254395,
   -0.10641133785247803,
   -0.14593839645385742,
   0.007471799850463867,
   -0.26851582527160645,
   -0.1841599941253662,
   -0.17872071266174316,
   -0.3929044008255005,
   -0.2823770046234131,
   -0.22108948230743408,
   -0.16696655750274658,
   -0.239967942237854,
   -0.16332519054412842,
   -0.26829326152801514,
   -0.3974398374557495,
   -0.20448815822601318,
   -0.40083229541778564,
   -0.3676292896270752,
   -0.22236740589141846,
   -0.2781393527984619,
   -0.38793957233428955,
   -0.33628296852111816,
   -0.044364333152770996,
   -0.014873147010803223,
   -0.19993996620178223,
   -0.38003575801849365,
   -0.2301539182662964,
   -0.46441924571990967,
   -0.4309579133987427,
   -0.288796067237

In [18]:
sample_data = sample_data.map(prepare_dataset, remove_columns=sample_data.column_names["train"])


Map:   0%|          | 0/2 [00:00<?, ? examples/s]

Map:   0%|          | 0/2 [00:00<?, ? examples/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (1028 > 1024). Running this sequence through the model will result in indexing errors


In [24]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")


In [25]:
model.generation_config.language = "arabic"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None

In [26]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [27]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)

In [28]:
import evaluate

metric = evaluate.load("wer")


In [31]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [29]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="dana2002/last-one",  # change to a repo name of your choice
    per_device_train_batch_size=2,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=1000,
    gradient_checkpointing=True,
    fp16=False,
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)

In [32]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=sample_data["train"],
    eval_dataset=sample_data["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor
)

max_steps is given, it will override any value given in num_train_epochs


In [33]:
trainer.train()


  0%|          | 0/1000 [00:00<?, ?it/s]

c:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


RuntimeError: The size of tensor a (843) must match the size of tensor b (448) at non-singleton dimension 1

##### Still same error.

### Plan B

In [3]:
from datasets import Features, Value, Audio, load_dataset

sample_data = load_dataset(
    'csv', data_files={
        'train': 'just-train.csv', 
        'test': 'just-test.csv',
    }
)

In [4]:
features = Features(
    {
        "Transcripts": Value("string"), 
        "Audio_File": Value('string'),
        "TA_ID": Value("int32"),
        "audio": Audio(sampling_rate=16000),
        "audio_wav": Audio(sampling_rate=16000)
    }
)

In [6]:
sample_data = sample_data.cast(features)
sample_data

Casting the dataset:   0%|          | 0/2 [00:00<?, ? examples/s]

Casting the dataset:   0%|          | 0/2 [00:00<?, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 2
    })
    test: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 2
    })
})

Whisper FE performs both padding + conversion in just this one line of code:

In [4]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")
feature_extractor

WhisperFeatureExtractor {
  "chunk_length": 30,
  "feature_extractor_type": "WhisperFeatureExtractor",
  "feature_size": 80,
  "hop_length": 160,
  "n_fft": 400,
  "n_samples": 480000,
  "nb_max_frames": 3000,
  "padding_side": "right",
  "padding_value": 0.0,
  "processor_class": "WhisperProcessor",
  "return_attention_mask": false,
  "sampling_rate": 16000
}

In [11]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained(
    "openai/whisper-small",
    language="Arabic",
    task="transcribe",
    pad_token = str(0),
    model_max_length=2000
)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [12]:
input_str = sample_data["train"][0]["Transcripts"]
labels = tokenizer(input_str).input_ids
decoded_with_special = tokenizer.decode(labels, skip_special_tokens=False)
decoded_str = tokenizer.decode(labels, skip_special_tokens=True)

print(f"Input:                 {input_str}")
print(f"Decoded w/ special:    {decoded_with_special}")
print(f"Decoded w/out special: {decoded_str}")
print(f"Are equal:             {input_str == decoded_str}")



Input:                  قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            
Decoded w/ special:    <|startoftranscript|><|ar|><|transcribe|><|notimestamps|> قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم

In [13]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Arabic", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [14]:
sample_data = sample_data.remove_columns("audio")
sample_data

DatasetDict({
    train: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio_wav'],
        num_rows: 2
    })
    test: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio_wav'],
        num_rows: 2
    })
})

Setting inputs to corect SR (= 16k HZ)

In [15]:
from datasets import Audio

sample_data = sample_data.cast_column("audio_wav", Audio(sampling_rate=16000))
sample_data['train'][0]

{'Transcripts': ' قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            ',
 'Audio_File': ' https://www.ireadarabic.com/uploads/slides/528/8449895552ae0361f230c080dc19096f.mp3',
 'TA_ID': 81615,
 'audio_wav': {'path': 'D:\\GP1\\.venv\\ipynb_Files\\Code\\tr

In [16]:
o = tokenizer(sample_data['train']["Transcripts"]).input_ids
for i in o:
    print(len(o))

2
2


In [17]:
#tokenizer

def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio_wav"]

    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]
    # encode target text to label ids 
    
    batch["labels"] = tokenizer(batch["Transcripts"]).input_ids
    # check.append(batch["labels"])
    
    return batch


In [18]:
sample_data = sample_data.map(prepare_dataset, remove_columns=sample_data.column_names["train"])


In [19]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")

In [20]:
model.generation_config.language = "arabic"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None

In [29]:
sample_data['train']

Dataset({
    features: ['input_features', 'labels'],
    num_rows: 2
})

In [ ]:
input_features = [{"input_features": feature["input_features"]} for feature in features]


In [33]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors

        input_features = [{"input_features": feature["input_features"]} for feature in features]

        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")
        

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [34]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor, decoder_start_token_id=model.config.decoder_start_token_id)

# Apply the data collator to your dataset
padded_batch = data_collator(sample_data["train"])


In [46]:
padded_input_features = padded_batch["input_features"]
len(padded_input_features[1])

80

In [22]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)

In [23]:
data_collator

DataCollatorSpeechSeq2SeqWithPadding(processor=WhisperProcessor:
- feature_extractor: WhisperFeatureExtractor {
  "chunk_length": 30,
  "feature_extractor_type": "WhisperFeatureExtractor",
  "feature_size": 80,
  "hop_length": 160,
  "n_fft": 400,
  "n_samples": 480000,
  "nb_max_frames": 3000,
  "padding_side": "right",
  "padding_value": 0.0,
  "processor_class": "WhisperProcessor",
  "return_attention_mask": false,
  "sampling_rate": 16000
}

- tokenizer: WhisperTokenizer(name_or_path='openai/whisper-small', vocab_size=50258, model_max_length=1024, is_fast=False, padding_side='right', truncation_side='right', special_tokens={'bos_token': '<|endoftext|>', 'eos_token': '<|endoftext|>', 'unk_token': '<|endoftext|>', 'pad_token': '<|endoftext|>', 'additional_special_tokens': ['<|endoftext|>', '<|startoftranscript|>', '<|en|>', '<|zh|>', '<|de|>', '<|es|>', '<|ru|>', '<|ko|>', '<|fr|>', '<|ja|>', '<|pt|>', '<|tr|>', '<|pl|>', '<|ca|>', '<|nl|>', '<|ar|>', '<|sv|>', '<|it|>', '<|id|>', '<

In [24]:
import evaluate

metric = evaluate.load("wer")

In [25]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [26]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="dana2002/myfinal",  # change to a repo name of your choice
    # per_device_train_batch_size=2,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    # max_steps=1000,
    gradient_checkpointing=True,
    fp16=False,
    evaluation_strategy="steps",
    # per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=2000,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=True,
)

In [27]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=sample_data["train"],
    eval_dataset=sample_data["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor
)

In [28]:
trainer.train()


  0%|          | 0/3 [00:00<?, ?it/s]

c:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


RuntimeError: The size of tensor a (843) must match the size of tensor b (448) at non-singleton dimension 1

In [73]:
model

WhisperForConditionalGeneration(
  (model): WhisperModel(
    (encoder): WhisperEncoder(
      (conv1): Conv1d(80, 768, kernel_size=(3,), stride=(1,), padding=(1,))
      (conv2): Conv1d(768, 768, kernel_size=(3,), stride=(2,), padding=(1,))
      (embed_positions): Embedding(1500, 768)
      (layers): ModuleList(
        (0-11): 12 x WhisperEncoderLayer(
          (self_attn): WhisperSdpaAttention(
            (k_proj): Linear(in_features=768, out_features=768, bias=False)
            (v_proj): Linear(in_features=768, out_features=768, bias=True)
            (q_proj): Linear(in_features=768, out_features=768, bias=True)
            (out_proj): Linear(in_features=768, out_features=768, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
          (activation_fn): GELUActivation()
          (fc1): Linear(in_features=768, out_features=3072, bias=True)
          (fc2): Linear(in_features=3072, out_features=768, bias=True)
        

### 1 audio file trial:

In [7]:
import pandas as pd

d1 = pd.read_csv(r"D:\GP1\.venv\ipynb_Files\Code\training-4whisper.csv")
try1 = d1[:1]
try1.head()

Transcripts  \
0   قالت باختصار شديد  والدكم قرر ترك عمله في الخ...   

                                          Audio_File  TA_ID  \
0   https://www.ireadarabic.com/uploads/slides/52...  81615   

                                              audio  \
0  D:\GP1\.venv\ipynb_Files\Code\Audios-1\81615.mp3   

                                           audio_wav  
0  D:\GP1\.venv\ipynb_Files\Code\train-wav\81615.wav

In [2]:
d1 = pd.read_csv(r"D:\GP1\.venv\ipynb_Files\Code\testing-4whisper.csv")
try2 = d1[:1]
try2.head()

Transcripts  \
0   تفوح منه رائحة الليمون                       ...   

                                          Audio_File  TA_ID  \
0   https://www.ireadarabic.com/uploads/slides/92...   1860   

                                               audio  \
0  D:\GP1\.venv\ipynb_Files\Code\Test-Audio\1860.mp3   

                                         audio_wav  
0  D:\GP1\.venv\ipynb_Files\Code\test-wav\1860.wav

In [3]:
# try1.to_csv('one-train.csv', index=False)
# try2.to_csv('one-test.csv', index=False)

In [1]:
from datasets import Features, Value, Audio, load_dataset

sd = load_dataset(
    'csv', data_files={
        'train': 'one-train.csv', 
        'test': 'one-test.csv',
    }
)

In [19]:
features = Features(
    {
        "Transcripts": Value("string"), 
        "Audio_File": Value('string'),
        "TA_ID": Value("int32"),
        "audio": Audio(sampling_rate=16000),
        "audio_wav": Audio(sampling_rate=16000)
    }
)

In [20]:
sd = sd.cast(features)
sd

DatasetDict({
    train: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 1
    })
    test: Dataset({
        features: ['Transcripts', 'Audio_File', 'TA_ID', 'audio', 'audio_wav'],
        num_rows: 1
    })
})

In [21]:
from transformers import WhisperFeatureExtractor

feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-small")


In [22]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-small", language="Arabic", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [23]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-small", language="Arabic", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [24]:
sd['train'][0]

{'Transcripts': ' قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            ',
 'Audio_File': ' https://www.ireadarabic.com/uploads/slides/528/8449895552ae0361f230c080dc19096f.mp3',
 'TA_ID': 81615,
 'audio': {'path': 'D:\\GP1\\.venv\\ipynb_Files\\Code\\Audios

In [16]:
# from datasets import Audio

# sd = sd.cast_column("audio_wav", Audio(sampling_rate=16000))


In [17]:
sd['train'][0]

{'Transcripts': ' قالت باختصار شديد  والدكم قرر ترك عمله في الخارج والعودة للعيش معنا هنا لقد رتب الأمور مع خالكم سوف يأتي غدا صباحا                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            ',
 'Audio_File': ' https://www.ireadarabic.com/uploads/slides/528/8449895552ae0361f230c080dc19096f.mp3',
 'TA_ID': 81615,
 'audio': {'path': 'D:\\GP1\\.venv\\ipynb_Files\\Code\\Audios

In [26]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio_wav"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = feature_extractor(audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids 
    batch["labels"] = tokenizer(batch["Transcripts"],padding=True,truncation=True,max_length=50, add_special_tokens=True).input_ids
    return batch


In [27]:
sd = sd.map(prepare_dataset, remove_columns=sd.column_names["train"])


Map:   0%|          | 0/1 [00:00<?, ? examples/s]

Map:   0%|          | 0/1 [00:00<?, ? examples/s]

In [28]:
len(sd['train']['input_features'][0])

80

In [29]:
len(sd['train']['labels'][0])

50

In [30]:
len(sd['test']['input_features'][0])

80

In [31]:
len(sd['test']['labels'][0])

50

In [32]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-small")


In [33]:
model.generation_config.language = "arabic"
model.generation_config.task = "transcribe"

model.generation_config.forced_decoder_ids = None


__call__ method takes list of feature where each feature is a dictionary containing "input_features" (audio inputs) & "labels" (tokenized label sequences).

In [34]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

from torch.nn.utils.rnn import pad_sequence

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any
    decoder_start_token_id: int

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]

        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length


        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")


        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)
      

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.decoder_start_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [35]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(
    processor=processor,
    decoder_start_token_id=model.config.decoder_start_token_id,
)


In [36]:
import evaluate

metric = evaluate.load("wer")


In [37]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [41]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="dana2002/myfinal",  # change to a repo name of your choice
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=1000,
    gradient_checkpointing=True,
    fp16=False,
    evaluation_strategy="steps",
    per_device_eval_batch_size=1,
    predict_with_generate=True,
    generation_max_length=50,
    save_steps=500,
    eval_steps=500,
    # logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=False,
)

In [42]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=sd["train"],
    eval_dataset=sd["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)


max_steps is given, it will override any value given in num_train_epochs


In [43]:
trainer.train()

  0%|          | 0/1000 [00:00<?, ?it/s]

c:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


KeyboardInterrupt: 

In [31]:
model

WhisperForConditionalGeneration(
  (model): WhisperModel(
    (encoder): WhisperEncoder(
      (conv1): Conv1d(80, 768, kernel_size=(3,), stride=(1,), padding=(1,))
      (conv2): Conv1d(768, 768, kernel_size=(3,), stride=(2,), padding=(1,))
      (embed_positions): Embedding(1500, 768)
      (layers): ModuleList(
        (0-11): 12 x WhisperEncoderLayer(
          (self_attn): WhisperSdpaAttention(
            (k_proj): Linear(in_features=768, out_features=768, bias=False)
            (v_proj): Linear(in_features=768, out_features=768, bias=True)
            (q_proj): Linear(in_features=768, out_features=768, bias=True)
            (out_proj): Linear(in_features=768, out_features=768, bias=True)
          )
          (self_attn_layer_norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
          (activation_fn): GELUActivation()
          (fc1): Linear(in_features=768, out_features=3072, bias=True)
          (fc2): Linear(in_features=3072, out_features=768, bias=True)
        